In [46]:
# import necessary libraries
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt 
from scipy.optimize import brentq
from mpl_toolkits.mplot3d import Axes3D
from matplotlib.animation import FuncAnimation
from IPython.display import HTML

In [280]:
# constants
G = 6.6743e-11 #(m^3)/(kg*s^2)
def binary(a,e,mu):
    """
    uses keplers equations to solve for the x,y positions of a binary star system within a plane (2D)
    """
    points = 100 # data points for simulation
    n = np.sqrt((G*(m1+m2))/(a**3))
    T = np.sqrt((4*np.pi**2*a**3)/(G*(m1+m2)))
    t = np.linspace(0,T,points)
    M = n*t
    def keplers_equation(M, e):
        E = np.zeros(len(M))
        """
        uses keplers equation to solve for E
        """
        for i in range(len(M)):
            Mi = M[i]
            def f(Ei):
                """
                defines a function in which keplers equation = 0
                """
                return Ei - e*np.sin(Ei)-Mi

            E[i] = brentq(f, Mi+e, Mi-e) # from scipy 
        return E
    E = keplers_equation(M,e)
    nu = 2*np.arctan2(np.sqrt(1+e)*np.sin(E/2), np.sqrt(1-e)*np.cos(E/2))
    r = (a*(1-e**2))/(1+e*np.cos(E)) # scalar distance between both masses
    r1 = ((m2)/(m1+m2))*r # distance of star1 from barycenter
    r2 = ((m1)/(m1+m2))*r # distance of star2 from barycenter
    x1 = r1*np.cos(nu) # cartesian transformation: x coordinate of star1 relative to barycenter 
    y1 = r1*np.sin(nu) # cartesian transformation: y coordinate of star1 relative to barycenter 
    x2 = -r2*np.cos(nu) # cartesian transformation: x coordinate of star2 relative to barycenter 
    y2 = -r2*np.sin(nu) # cartesian transformation: y coordinate of star2 relative to barycenter 
    a1 = ((m2)/(m1+m2))*a # semi-major axis of star1 from barycenter
    a2 = ((m1)/(m1+m2))*a # semi-major axis of star2 from barycenter
    v1 = np.sqrt(G*(m1+m2)*((2/r1)-(1/a1))) # orbital velocity of star1 (see vis-via)
    v2 = np.sqrt(G*(m1+m2)*((2/r2)-(1/a2))) # orbital velocity of star2 (see vis-via)
    KE1 = (0.5)*(m1)*(v1**2) # kinetic energy of star1
    KE2 = (0.5)*(m2)*(v2**2) # kinetic energy of star2
    KE = KE1 + KE2 # relative kinetic energy 
    U = -(G*(m1*m2))/(r) # gravitational potential energy of system from Newtons law of gravity
    ME = -(G*(m1*m2))/(2*a) # total mechanical energy within the closed system (should be relatively constant in this simulation)
    dv1dt = ((G*m2)/(r**2)) # acceleration magnitude of star1
    dv2dt = ((G*m1)/(r**2)) # acceleration magnitude of star2
    accel = dv1dt + dv2dt # relative acceleration
    
    
    return x1, y1, x2, y2, T, t, r, r1, r2, v1, v2, KE1, KE2, KE, U, ME, dv1dt, dv2dt, accel

def run(a,e,mu):
    x1, y1, x2, y2, T, t, r, r1, r2, v1, v2, KE1, KE2, KE, U, ME, dv1dt, dv2dt, accel = binary(a,e,mu)
    fig, ax = plt.subplots(figsize=(6,6), facecolor='black')
    ax.set_facecolor('black')
    ax.plot(x1, y1, 'b--', label='star 1 orbit', alpha=0.4)
    ax.plot(x2, y2, color='dodgerblue', linestyle='--', alpha=0.4, label='star 2 orbit')
    star1, = ax.plot([], [], color='r', label='star 1', marker='o', markersize=15)
    star2, = ax.plot([], [], color='yellow', label='star 2', marker='o', markersize=15)
    path1, = ax.plot([], [], color='blue', label='orbital path of star1', linestyle='-', alpha=0.8)
    path2, = ax.plot([], [], color='dodgerblue', label='orbital path of star2', linestyle='-', alpha=0.8)
    time = ax.text(0.1, 0.9, '', transform=ax.transAxes, color='white')
    ax.set_aspect('equal', adjustable='box')
    ax.set_xlabel('x position (m)', color='white')
    ax.set_ylabel('y position (m)', color='white')
    ax.set_title('Binary Star System', color='white')
    ax.tick_params(colors='white')


    def init():
        star1.set_data([], [])
        star2.set_data([], [])
        path1.set_data([], [])
        path2.set_data([], [])
        time.set_text('')
        return star1, star2, path1, path2, time

    def update(frame):
        star1.set_data([x1[frame]], [y1[frame]])
        star2.set_data([x2[frame]], [y2[frame]])
        path1.set_data([x1[:frame+1]], [y1[:frame+1]])
        path2.set_data([x2[:frame+1]], [y2[:frame+1]])
        time.set_text(f"Time: {t[frame]/86400:.1f} days")
        return star1, star2, path1, path2, time
    speed = 1
    frames = range(0,len(x1),1)
    anim = FuncAnimation(fig, update, frames=frames, init_func=init, interval=60, blit=True, repeat=True)
    plt.savefig("binarystar2D_plot.png", dpi=300, bbox_inches='tight', facecolor=fig.get_facecolor())
    plt.close(fig)  
    return HTML(anim.to_jshtml())  

a = 3.5e12 # m (semi-major axis for alpha A & B system)
e = 0.52 # estimated eccentricity for alpha A & B system
m1 = 2.19e30 # kg (representing alpha centauri A)
m2 = 1.81e30 # kg (representing alpha centauri B)
mu = G*(m1+m2) 

run(a,e,mu)